# Inference

In [2]:
import json
import nltk
from nltk.tokenize import sent_tokenize
import torch

In [3]:
from peft import PeftModel, PeftConfig
from transformers import AutoModelForCausalLM, AutoTokenizer

peft_model_id = "/home/tian/Projects/BioRED/peft/biogpt_peft"
config = PeftConfig.from_pretrained(peft_model_id)
model = AutoModelForCausalLM.from_pretrained("/home/tian/Projects/BioRED/peft/model-bio", return_dict=True, load_in_8bit=True)

# Load the Lora model
model = PeftModel.from_pretrained(model, peft_model_id)

tokenizer = AutoTokenizer.from_pretrained("/home/tian/Projects/BioRED/peft/biogpt_peft/tokenizer")

/home/tian/mambaforge/envs/BioGPT/lib/python3.10/site-packages/bitsandbytes/cuda_setup/main.py:149: UserWarning: Found duplicate ['libcudart.so', 'libcudart.so.11.0', 'libcudart.so.12.0'] files: {PosixPath('/home/tian/mambaforge/envs/BioGPT/lib/libcudart.so.11.0'), PosixPath('/home/tian/mambaforge/envs/BioGPT/lib/libcudart.so')}.. We'll flip a coin and try one of these, in order to fail forward.
Either way, this might cause trouble in the future:
If you get `CUDA error: invalid device function` errors, the above might be the cause and the solution is to make sure only one ['libcudart.so', 'libcudart.so.11.0', 'libcudart.so.12.0'] in the paths that we search based on your env.
  warn(msg)
You passed `quantization_config` to `from_pretrained` but the model you're loading already has a `quantization_config` attribute. The `quantization_config` attribute will be overwritten with the one you passed to `from_pretrained`.



===================================BUG REPORT===================================
Welcome to bitsandbytes. For bug reports, please run

python -m bitsandbytes

 and submit this information together with your error trace to: https://github.com/TimDettmers/bitsandbytes/issues
bin /home/tian/mambaforge/envs/BioGPT/lib/python3.10/site-packages/bitsandbytes/libbitsandbytes_cuda118.so
CUDA SETUP: CUDA runtime path found: /home/tian/mambaforge/envs/BioGPT/lib/libcudart.so.11.0
CUDA SETUP: Highest compute capability among GPUs detected: 8.6
CUDA SETUP: Detected CUDA version 118
CUDA SETUP: Loading binary /home/tian/mambaforge/envs/BioGPT/lib/python3.10/site-packages/bitsandbytes/libbitsandbytes_cuda118.so...


Some weights of the model checkpoint at /home/tian/Projects/BioRED/peft/model-bio were not used when initializing BioGptForCausalLM: ['biogpt.layers.16.self_attn.q_proj.lora_A.default.weight', 'biogpt.layers.15.self_attn.q_proj.lora_B.default.weight', 'biogpt.layers.7.self_attn.v_proj.lora_B.default.weight', 'biogpt.layers.7.self_attn.q_proj.lora_B.default.weight', 'biogpt.layers.1.self_attn.v_proj.lora_B.default.weight', 'biogpt.layers.3.self_attn.v_proj.lora_A.default.weight', 'biogpt.layers.12.self_attn.q_proj.lora_B.default.weight', 'biogpt.layers.23.self_attn.q_proj.lora_A.default.weight', 'biogpt.layers.11.self_attn.v_proj.lora_B.default.weight', 'biogpt.layers.6.self_attn.v_proj.lora_A.default.weight', 'biogpt.layers.10.self_attn.v_proj.lora_A.default.weight', 'biogpt.layers.12.self_attn.v_proj.lora_A.default.weight', 'biogpt.layers.15.self_attn.v_proj.lora_B.default.weight', 'biogpt.layers.16.self_attn.v_proj.lora_B.default.weight', 'biogpt.layers.9.self_attn.q_proj.lora_B.defa

In [4]:
model.to("cuda")

PeftModelForCausalLM(
  (base_model): LoraModel(
    (model): BioGptForCausalLM(
      (biogpt): BioGptModel(
        (embed_tokens): Embedding(42388, 1024, padding_idx=1)
        (embed_positions): BioGptLearnedPositionalEmbedding(1026, 1024)
        (layers): ModuleList(
          (0-23): 24 x BioGptDecoderLayer(
            (self_attn): BioGptAttention(
              (k_proj): Linear8bitLt(in_features=1024, out_features=1024, bias=True)
              (v_proj): Linear8bitLt(
                in_features=1024, out_features=1024, bias=True
                (lora_dropout): ModuleDict(
                  (default): Dropout(p=0.02, inplace=False)
                )
                (lora_A): ModuleDict(
                  (default): Linear(in_features=1024, out_features=16, bias=False)
                )
                (lora_B): ModuleDict(
                  (default): Linear(in_features=16, out_features=1024, bias=False)
                )
                (lora_embedding_A): ParameterDict()
   

In [5]:
# src_file = 'data/KD-DTI/raw/optimized_tokenization_test.x.json'
# with open(src_file) as reader:
#      src_inputs_ids = json.load(reader)

src_file = "/home/tian/Projects/BioGPT/data/KD-DTI/raw/test.json"
src_inputs = []
with open(src_file) as reader:
    src_inputs = json.load(reader)

src_inputs_text = []
for k in src_inputs.keys():
    title = src_inputs[k]['title'].strip()
    if title[-1] != ".":
        title += "."
    text = title + " " + src_inputs[k]['abstract'].strip()
    sentences = sent_tokenize(text)
    text = ""
    for sent in sentences:
        text_temp = text + sent[:-1] + " . " 
        if len(tokenizer.encode(text_temp, return_tensors="pt")[-1]) < 900:
            text = text_temp
        else:
            break

    text = text[:-1]
    answer = " [learn1] [learn2] [learn3] [learn4] "
    text = text + answer
    src_inputs_text.append(text)

In [6]:
len(src_inputs_text)

1159

In [29]:
import time

outputs = []

In [30]:
for n, input in enumerate(src_inputs_text):
  start_time = time.time()
  batch = tokenizer(input, return_tensors='pt')
  batch['input_ids'] = batch['input_ids'].to("cuda")
  batch['attention_mask'] = batch['attention_mask'].to("cuda")
  with torch.cuda.amp.autocast():
    output_tokens = model.generate(**batch, max_new_tokens=100)

  # out_text = truncate_string(tokenizer.decode(output_tokens[0], skip_special_tokens=True))
  # outputs.append(tokenizer.decode(output_tokens[0], skip_special_tokens=True))
  outputs.append(output_tokens[0])
  elapsed_time = time.time() - start_time
  print(f"{n + 1} / {len(src_inputs_text)}, {elapsed_time:.2f}s")
  # if n % 100 == 0:
  #   with open(f"outputs-peft-{n}.json", "w") as writer:
  #     json.dump(outputs, writer)
      # outputs = []

1 / 1159, 13.79s
2 / 1159, 13.28s
3 / 1159, 12.93s
4 / 1159, 12.64s
5 / 1159, 12.56s
6 / 1159, 12.59s
7 / 1159, 12.51s
8 / 1159, 12.58s
9 / 1159, 12.58s
10 / 1159, 12.73s
11 / 1159, 12.65s
12 / 1159, 12.54s
13 / 1159, 12.61s
14 / 1159, 12.54s
15 / 1159, 12.59s
16 / 1159, 12.65s
17 / 1159, 12.59s
18 / 1159, 12.58s
19 / 1159, 12.83s
20 / 1159, 12.49s
21 / 1159, 12.64s
22 / 1159, 12.70s
23 / 1159, 12.71s
24 / 1159, 12.79s
25 / 1159, 12.75s
26 / 1159, 12.64s
27 / 1159, 12.41s
28 / 1159, 12.18s
29 / 1159, 12.42s
30 / 1159, 12.22s
31 / 1159, 12.20s
32 / 1159, 12.25s
33 / 1159, 12.70s
34 / 1159, 12.44s
35 / 1159, 12.09s
36 / 1159, 12.30s
37 / 1159, 12.23s
38 / 1159, 12.14s
39 / 1159, 12.21s
40 / 1159, 12.23s
41 / 1159, 12.27s
42 / 1159, 12.21s
43 / 1159, 12.47s
44 / 1159, 12.25s
45 / 1159, 12.27s
46 / 1159, 12.27s
47 / 1159, 12.79s
48 / 1159, 12.51s
49 / 1159, 12.26s
50 / 1159, 12.18s
51 / 1159, 12.22s
52 / 1159, 12.49s
53 / 1159, 12.29s
54 / 1159, 12.29s
55 / 1159, 12.15s
56 / 1159, 12.22s
5

In [31]:
outputs

[tensor([    2,  4159,     5,   366,   251, 12156,  3183,   619,    23, 34292,
         25183,     8, 15443, 10573, 25183,    20,  1468,    16,     6,    53,
             5,  6042,   632,     4,   321, 10573, 25183,     8, 15443, 10573,
         25183,     7, 35045, 26361,  1578,   451,    29,     6,  1041,   321,
         10573,   846,  5263,  4032,  1511, 23484,  4797,     7,    19,   301,
            13,  2171,    10,   307,  1166,  2247,    25, 12156,  3183,    12,
         12406,    11,   619,    10,   366,   251,  2754,     7,  5899,  3313,
         12406,     9,    39,    79,   222, 12406,     9,   152,    79,     4,
            56,   468,     5,   439,   619,    17,    95,    13,    33,   228,
             9,   267,     8,  3599,     4,   551, 12406,     9,    39,     7,
             6,  6011,   358,    31, 17239,    51,    26,    81,  2865,  1417,
         34292, 25183,     8,  7160,    51,    26,    81,  3010,  1417, 15443,
         10573, 25183,     4,   551, 12406,     9,  

In [133]:
import re

# def truncate_string(string):
#     pattern = r"The interaction between(.*?)\.(?: The| the)"
#     match = re.search(pattern, string, re.IGNORECASE)
#     if match:
#         truncated_string = match.group()[:-1] + "."
#         return truncated_string
#     else:
#         return string
    
def truncate_string(text):
    count = 0
    start = None
    end = None
    for i, chara in enumerate(text):
        if chara == "[" and text[i: i+8] == "[learn4]" and count == 0:
            start = i + 9
            count += 1
            # print(text[start])
        try:
            if chara == "." and (text[i:i+4] == ". Th" or text[i:i+4] == ". th") and count == 1:
                end = i + 1
                break
        except:
            end = len(text) - 1
            break
    return text[start:end]


In [134]:
truncate_string(tokenizer.decode(outputs[0], skip_special_tokens=False))

'The interaction between Psoralen and Monoamine oxidase type A is inhibitor; The interaction between Psoralen and Monoamine oxidase type B is inhibitor.'

In [136]:
output_texts = [truncate_string(tokenizer.decode(tensor, skip_special_tokens=False)) for tensor in outputs]
output_texts = [text.lower() for text in output_texts]

In [138]:
len(output_texts)

1159

In [139]:
with open(f"{'examples/RE-DTI/generate_checkpoint_peft.pt.detok'}", "w", encoding='utf8') as fw:
    for i in range(len(output_texts)):
        fw.write(output_texts[i] + '\n')

sed -i "s/@@ //g" generate_checkpoint_peft.pt

perl ../../mosesdecoder/scripts/tokenizer/detokenizer.perl -l en -a < generate_checkpoint_peft.pt > generate_checkpoint_peft.pt.detok

# post process

In [140]:
import os
import sys
import re
import json

In [141]:
out_file = 'examples/RE-DTI/generate_checkpoint_peft.pt.detok'

In [143]:
prefix = [
    r'\[learned[0-9]\]',
    'we can conclude that',
    'we have that',
    'in conclusion,',
    ]

In [144]:
def strip_prefix(line: str) -> str:
    """Removes the prefix from the line."""
    # search for the prefix in the line
    for p in prefix:
        res = re.search(p, line)
        
        if res is not None:
            # remove the prefix from the line
            line = re.split(p, line)[-1].strip()
            break
    return line

In [145]:
def split_sentence(line):
    """Splits the line into sentences by semicolon."""
    sentences = re.split(r"; ", line)
    return sentences

In [146]:
def convert_relis_sentence(sentence):
    # match sentences of the form "the interaction between X and Y is Z"
    # and return the tuple (X, Z, Y)
    ans = None
    segs = re.match(r"the interaction between (.*) and (.*) is (.*)", sentence)
    if segs is not None:
        segs = segs.groups()
        ans = (segs[0].strip(), segs[2].strip(), segs[1].strip())
    return ans

In [147]:
def converter(sample, head_idx=0, rel_idx=1, tail_idx=2):
    ret = {
        "triple_list_gold": [], 
        "triple_list_pred": [], 
        "new": [], 
        "lack": [], 
        "id": [0]
    }
    for item in sample:
        ret["triple_list_pred"].append(
            {"subject": item[head_idx], 
            "relation": item[rel_idx], 
            "object": item[tail_idx]}
        )
    return ret

In [148]:
all_lines = []
with open(out_file, "r", encoding="utf8") as fr:
    for line in fr:
        e = line.strip()
        if len(e) > 0 and e[-1] == ".": # if the last character of the line is a period, remove it
            all_lines.append(e[:-1])
        else:
            all_lines.append(e)

print(f'Number of lines: {len(all_lines)}')

Number of lines: 1159


In [149]:
all_lines[0]

'the interaction between psoralen and monoamine oxidase type a is inhibitor; the interaction between psoralen and monoamine oxidase type b is inhibitor'

In [150]:
hypothesis = []
cnt = 0
fail_cnt = 0

In [151]:
# i is the index of the line in the input file
for i, line in enumerate(all_lines):
    # cnt is the number of lines in the input file
    cnt += 1
    ret = []
    # convert the "& amp" if it is in line to "&"
    line = line.replace(" & amp; ", "&")
    strip_line = strip_prefix(line)
    sentences = split_sentence(strip_line)
    for sen in sentences:
        ans = convert_relis_sentence(sen)
        if ans is not None:
            ret.append(ans)
    if len(ret) > 0:
        hypothesis.append(ret)
    else:
        hypothesis.append([("failed", "failed", "failed")])
        fail_cnt += 1
        print("Failed:id:{}, line:{}".format(i+1, line))

In [152]:
hypothesis[764]

[('plasminogen', 'activator', 'plasminogen activator inhibitor 1')]

In [153]:
ret_formatted = []
for i in range(len(hypothesis)):
    ret_formatted.append(converter(hypothesis[i]))

In [154]:
ret_formatted[764]

{'triple_list_gold': [],
 'triple_list_pred': [{'subject': 'plasminogen',
   'relation': 'activator',
   'object': 'plasminogen activator inhibitor 1'}],
 'new': [],
 'lack': [],
 'id': [0]}

In [155]:
with open(f"{out_file}.extracted.json", "w", encoding="utf8") as fw:
    for eg in ret_formatted:
        print(json.dumps(eg), file=fw)


print(f"failed = {fail_cnt}, total = {cnt}")

failed = 0, total = 1159


# Eval

In [156]:
import re
import json
import sys
import os

In [157]:
pred_file = 'examples/RE-DTI/generate_checkpoint_peft.pt.detok.extracted.json'
gold_file = 'data/KD-DTI/raw/test.json'
pmids_file = 'data/KD-DTI/raw/relis_test.pmid'

In [158]:
def normalize_name(s: str):
    s = s.strip()

    # normalize roman type id at end of string
    num2roman = {"0": "0", "1": "I", "2": "II", "3": "III", "4": "IV", "5": "V", "6": "VI", "7": "VII", "8": "VIII", "9": "IX"}
    if len(s) > 2 and s[-1].isnumeric() and not s[-2].isnumeric() and s[-1] in num2roman:
        tmps = list(s)
        s = ''.join(tmps[:-1]) + num2roman[tmps[-1]]

    # remove useless end string
    s = s.replace("-type", '')
    
    # remove non-alphanumeric characters
    return re.sub('[^a-zA-Z0-9]+', '', s)

In [159]:
# e.p. for normalize_name

print(f"trace amine-associated receptor 1 (taar1)\n{normalize_name('trace amine-associated receptor 1 (taar1)')}\n\ntrace amine-associated receptor 1\n{normalize_name('trace amine-associated receptor 1')}\n\ntrace amine-associated receptor 21\n{normalize_name('trace amine-associated receptor 21')}")

trace amine-associated receptor 1 (taar1)
traceamineassociatedreceptor1taar1

trace amine-associated receptor 1
traceamineassociatedreceptorI

trace amine-associated receptor 21
traceamineassociatedreceptor21


In [160]:
def rm_abbr(tgt_set):
    """ remove abbreviation in the brackets of entity, eg: aaa (bb) -> aaa """
    def rm(s):
        s = s.strip()
        if "(" in s and s[-1] == ')':  # entity end with a bracketed short cut
            return normalize_name(s[:s.rfind("(")].strip())
        else:
            return normalize_name(s)

    tgt_set = list(tgt_set)
    if tgt_set and type(tgt_set[0]) in [tuple, list]:  # process triples
        return set([(rm(tp[0]), rm(tp[1]), rm(tp[2])) for tp in tgt_set])
    else:  # process entities
        return set([rm(e) for e in tgt_set])

In [161]:
def get_abbr(tgt_set):
    """ extract abbreviation in the brackets of entity, eg: aaa (bb) -> bb """
    def rm(s):
        s = s.strip()
        if "(" in s and s[-1] == ')':
            return normalize_name(s[s.rfind("(")+1:-1].strip())
        else:
            return normalize_name(s)

    tgt_set = list(tgt_set)
    if tgt_set and type(tgt_set[0]) in [tuple, list]:  # process triples
        return set([(rm(tp[0]), rm(tp[1]), rm(tp[2])) for tp in tgt_set])
    else:  # process entities
        return set([rm(e) for e in tgt_set])

In [162]:
def acc(pred_set, gold_set):
    """ Multi-label style acc """
    tp_num = len(pred_set & gold_set)
    return int(pred_set == gold_set) if len(gold_set) == 0 else 1.0 * tp_num / len(pred_set | gold_set)


def precision(pred_set, gold_set):
    """ Multi-label style precision """
    tp_num = len(pred_set & gold_set)
    return int(pred_set == gold_set) if len(pred_set) == 0 else 1.0 * tp_num / len(pred_set)


def recall(pred_set, gold_set):
    """ Multi-label style recall """
    tp_num = len(pred_set & gold_set)
    return int(pred_set == gold_set) if len(gold_set) == 0 else 1.0 * tp_num / len(gold_set)


def normed_eval(pred_set, gold_set, metric):
    """ Both body and abbreviation match are considered correct """
    abbr_pred_set, abbr_gold_set = get_abbr(pred_set), get_abbr(gold_set)
    rm_pred_set, rm_gold_set = rm_abbr(pred_set), rm_abbr(gold_set)
    return max(metric(abbr_pred_set, abbr_gold_set), metric(rm_pred_set, rm_gold_set))


def get_f1(p, r):
    return 0 if (p + r) == 0 else (2.0 * p * r / (p + r))


def ave(scores):
    return 1.0 * sum(scores) / len(scores)

In [163]:
def do_eval(preds, pmids, golden):
    ret = []
    num_pred, num_gold, num_missing = 0, 0, 0
    all_f1, p, r, d_acc, t_acc, i_acc = [], [], [], [], [], []
    all_pred_triple, all_pred_d, all_pred_t, all_pred_i, all_gold_triple, all_gold_d, all_gold_t, all_gold_i = [], [], [], [], [], [], [], [],

    for pred, idx in zip(preds, pmids):
        # initialize a set for each entity type (drug, target, interaction) for the prediction and gold standard
        gold_d_set, gold_t_set, gold_i_set, gold_set = set(), set(), set(), set()
        pred_d_set, pred_t_set, pred_i_set, pred_set = set(), set(), set(), set()
        
        # if the prediction is not empty and if the model did not fail to extract any triple
        if pred["triple_list_pred"] and pred["triple_list_pred"][0]["subject"] != 'failed':
            # loop over all triples and add the entities to the respective sets
            for tp in pred["triple_list_pred"]:
                d = tp["subject"].strip().lower().replace(' ', '')
                t = tp["object"].strip().lower().replace(' ', '')
                i = tp["relation"].strip().lower().replace(' ', '')

                pred_d_set.add(d)
                pred_t_set.add(t)
                pred_i_set.add(i)
                pred_set.add((d, t, i))
        # if the paper is not in the golden set
        if idx not in golden:
            # increase the number of missing papers
            num_missing += 1
            # print a message
            print("----Missing:", idx)
            # skip this paper
            continue
        # if there are triples in the golden set
        if golden[idx]["triples"]:
            # loop over all triples and add the entities to the respective sets
            for tp in golden[idx]["triples"]:
                d = tp["drug"].strip().lower().replace(' ', '')
                t = tp["target"].strip().lower().replace(' ', '')
                i = tp["interaction"].strip().lower().replace(' ', '')
                gold_d_set.add(d)
                gold_t_set.add(t)
                gold_i_set.add(i)
                gold_set.add((d, t, i))

        # sample level eval
        p.append(normed_eval(pred_set, gold_set, metric=precision))
        r.append(normed_eval(pred_set, gold_set, metric=recall))
        all_f1.append(get_f1(p[-1], r[-1]))
        d_acc.append(normed_eval(pred_d_set, gold_d_set, metric=acc))
        t_acc.append(normed_eval(pred_t_set, gold_t_set, metric=acc))
        i_acc.append(normed_eval(pred_i_set, gold_i_set, metric=acc))

        # onto level eval
        all_pred_d.extend(pred_d_set)
        all_pred_t.extend(pred_t_set)
        all_pred_i.extend(pred_i_set)
        all_pred_triple.extend(pred_set)
        all_gold_d.extend(gold_d_set)
        all_gold_t.extend(gold_t_set)
        all_gold_i.extend(gold_i_set)
        all_gold_triple.extend(gold_set)
        
        # if len(gold_set) < len(golden[idx]["triples"]):
            # print("Duplicate extists, ori", golden[idx]["triples"], gold_set)

        num_pred += len(pred_set)
        num_gold += len(gold_set)

        ret.append({
            "pmid": idx,
            "title": golden[idx]["title"] if "title" in golden[idx] else None,
            "abstract": golden[idx]["abstract"],
            "d_pred_gold": [d_acc[-1], list(pred_d_set), list(gold_d_set)],
            "t_pred_gold": [t_acc[-1], list(pred_t_set), list(gold_t_set)],
            "i_pred_gold": [i_acc[-1], list(pred_i_set), list(gold_i_set)],
            "all_pred_gold": [all_f1[-1], list(pred_set), list(gold_set)],
        })


    print("num sample", len(all_f1), "missing", len(preds) - len(all_f1), "num_gold tp", num_gold, "num_pred", num_pred)

    # Note: we adopt multi-label metrics following: http://129.211.169.156/publication/tkde13rev.pdf
    print("Sample: acc d: {:.4f}\tt:{:.4f}\ti: {:.4f}\ntp p: {:.4f}\ttp r: {:.4f}\ttp micro f1: {:.4f}\ttp macro f1: {:.4f} ".format(
        ave(d_acc), ave(t_acc), ave(i_acc), ave(p), ave(r), ave(all_f1), get_f1(ave(p), ave(r))))

    # Ontology evaluation_scripts
    all_p, all_r = normed_eval(set(all_pred_triple), set(all_gold_triple), metric=precision), normed_eval(set(all_pred_triple), set(all_gold_triple), metric=recall)
    d_p, d_r = normed_eval(set(all_pred_d), set(all_gold_d), metric=precision), normed_eval(set(all_pred_d), set(all_gold_d), metric=recall)
    t_p, t_r = normed_eval(set(all_pred_t), set(all_gold_t), metric=precision), normed_eval(set(all_pred_t), set(all_gold_t), metric=recall)
    i_p, i_r = normed_eval(set(all_pred_i), set(all_gold_i), metric=precision), normed_eval(set(all_pred_i), set(all_gold_i), metric=recall)

    print("Ontology: f1 d: {:.4f}\tt:{:.4f}\ti: {:.4f}\t \nall p: {:.4f}\tall r: {:.4f}\tonto f1: {:.4f}".format(
        get_f1(d_p, d_r), get_f1(t_p, t_r), get_f1(i_p, i_r), all_p, all_r, get_f1(all_p, all_r)
    ))
    return ret

In [164]:
preds = []
with open(pred_file) as reader:
    for line in reader:
        preds.append(json.loads(line))

with open(gold_file) as reader:
    golden = json.load(reader)

with open(pmids_file) as reader:
    if '.json' in pmids_file:
        pmids = json.load(reader)
    else:
        pmids = []
        for line in reader:
            pmids.append(line.strip())

In [165]:
print("\n====File: ", os.path.basename(pred_file))


====File:  generate_checkpoint_peft.pt.detok.extracted.json


In [166]:
preds[0]

{'triple_list_gold': [],
 'triple_list_pred': [{'subject': 'psoralen',
   'relation': 'inhibitor',
   'object': 'monoamine oxidase type a'},
  {'subject': 'psoralen',
   'relation': 'inhibitor',
   'object': 'monoamine oxidase type b'}],
 'new': [],
 'lack': [],
 'id': [0]}

In [31]:
result = do_eval(preds, pmids, golden)

last_pos = pred_file.rfind('.json')
res_file_name = pred_file[:last_pos] + '.eval_res.json'

num sample 1159 missing 0 num_gold tp 1567 num_pred 2250
Sample: acc d: 0.6175	t:0.6067	i: 0.8667
tp p: 0.4009	tp r: 0.3980	tp micro f1: 0.3851	tp macro f1: 0.3994 
Ontology: f1 d: 0.6093	t:0.5122	i: 0.7556	 
all p: 0.2518	all r: 0.3735	onto f1: 0.3008


In [167]:
# new
result = do_eval(preds, pmids, golden)

last_pos = pred_file.rfind('.json')
res_file_name = pred_file[:last_pos] + '.eval_res.json'

num sample 1159 missing 0 num_gold tp 1567 num_pred 1539
Sample: acc d: 0.6073	t:0.5954	i: 0.8687
tp p: 0.3842	tp r: 0.3636	tp micro f1: 0.3633	tp macro f1: 0.3736 
Ontology: f1 d: 0.6208	t:0.5812	i: 0.7317	 
all p: 0.3246	all r: 0.3331	onto f1: 0.3288


In [81]:
with open(res_file_name, 'w') as writer:
    json.dump(result, writer, indent=2)

See the comparation of the outputs in:

examples/RE-DTI/generate_checkpoint_avg.pt.detok.extracted.eval_res.json

# Analysis

In [2]:
from transformers import BioGptTokenizer
tokenizer = BioGptTokenizer.from_pretrained("microsoft/biogpt")

/home/tian/mambaforge/envs/BioGPT/lib/python3.10/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [4]:
pred_file = 'examples/RE-DTI/generate_checkpoint_avg.pt.detok.extracted.json'
# gold_file = 'data/KD-DTI/raw/test.json'
gold_file = 'data/KD-DTI/raw/train.json'
# pmids_file = 'data/KD-DTI/raw/relis_test.pmid'
pmids_file = 'data/KD-DTI/raw/relis_train.pmid'

In [5]:
import json

preds = []
with open(pred_file) as reader:
    for line in reader:
        preds.append(json.loads(line))

with open(gold_file) as reader:
    golden = json.load(reader)

with open(pmids_file) as reader:
    if '.json' in pmids_file:
        pmids = json.load(reader)
    else:
        pmids = []
        for line in reader:
            pmids.append(line.strip())

In [9]:
golden[pmids[0]]

{'title': 'Beta-subunits co-determine the sensitivity of rat neuronal nicotinic receptors to antagonists.',
 'abstract': "We have investigated the effect of 4 ganglionic cholinergic antagonists (hexamethonium, mecamylamine, pentolinium, trimetaphan) on rat alpha 3 beta 2 and alpha 3 beta 4 neuronal nicotinic acetylcholine receptors (nAChRs) expressed in Xenopus oocytes. Current responses were elicited by fast application of acetylcholine on voltage-clamped oocytes (holding potentialVh = -80mV). Concentration-inhibition curves were used to get estimates of IC50, the antagonist concentration yielding 50% reduction of the peak current. The KB's of the antagonists were calculated using estimates of the apparent KD of acetylcholine. The order of affinity of the antagonists was similar for both receptor subtypes: mecamylamine approximately pentolinium &gt; hexamethonium &gt; trimetaphan. However, alpha 3 beta 4 neuronal nAChRs were 9 to 22 times more sensitive to each of the 4 antagonists th

In [94]:
preds[0]

{'triple_list_gold': [],
 'triple_list_pred': [{'subject': 'isopsoralen',
   'relation': 'inhibitor',
   'object': 'monoamine oxidase type b (mao-b)'},
  {'subject': 'isopsoralen',
   'relation': 'inhibitor',
   'object': 'monoamine oxidase type a (mao-a)'}],
 'new': [],
 'lack': [],
 'id': [0]}

In [100]:
num_pred_D = 0
num_pred_T = 0
num_gold_D = 0
num_gold_T = 0


num_predD_in_original = 0
num_predT_in_original = 0
# # if there are more than 50% prefix tokens of a span is in the original text, count it
# num_predD_over50_in_original = 0
# num_predT_over50_in_original = 0
# partial in the golden means the model didn't generate the whole span.
num_goldD_in_original = 0

predT_not_in_original_pmid_predTs = []

for id, pred in zip(pmids, preds):
    # only use lower() to nomalize the text
    pred_Ds = list(set([triple['subject'].lower() for triple in pred['triple_list_pred']]))
    pred_Ts = list(set([triple['object'].lower() for triple in pred['triple_list_pred']]))
    gold_Ds = list(set([triple['drug'].lower() for triple in golden[id]['triples']]))
    gold_Ts = list(set([triple['target'].lower() for triple in golden[id]['triples']]))
    text = (golden[id]['title'] + " " + golden[id]['abstract']).lower()
    
    num_pred_D += len(pred_Ds)
    num_pred_T += len(pred_Ts)
    num_gold_D += len(gold_Ds)
    num_gold_T += len(gold_Ts)

    predT_not_in_original = []

    # count for if pred_D in the original text
    for pred_D in pred_Ds:
        if pred_D is not None:
            if pred_D in text:
                num_predD_in_original += 1

    # count for if pred_T in the original text
    for pred_T in pred_Ts:
        if pred_T is not None:
            if pred_T in text:
                num_predT_in_original += 1
            else:
                predT_not_in_original.append(pred_T)


    # count for if god_D in the original text
    for gold_D in gold_Ds:
        if gold_D in text:
            num_goldD_in_original += 1

    # count for if god_T in the original text
    for gold_T in gold_Ts:
        if gold_T in text:
            num_goldT_in_original += 1


    if predT_not_in_original:
        predT_not_in_original_pmid_predTs.append({
            "id": id,
            "predT_not_in_original": predT_not_in_original
            })
    # pred_D_ids = [tokenizer.encode(pred_d, add_special_tokens=False) for pred_d in pred_Ds]
    # pred_T_ids = [tokenizer.encode(pred_t, add_special_tokens=False) for pred_t in pred_Ts]
    # gold_D_ids = [tokenizer.encode(gold_d, add_special_tokens=False) for gold_d in gold_Ds]
    # gold_T_ids = [tokenizer.encode(gold_t, add_special_tokens=False) for gold_t in gold_Ts]
    # text_id = tokenizer.encode(text, add_special_tokens=False)

    # # count for if pred_D in the original text
    # for pred_d_id in pred_D_ids:
    #     length = len(pred_d_id)
    #     for i in range(len(text_id)):
    #         for j in range(length):
    #             if text_id[i+j+1] == pred_d_id[:j+1]:
    #                 if j+1 == length:
    #                     num_predD_in_original += 1
    #             else:
    #                 if j+1 > length/2:
    #                     num_predD_over50_in_original += 1
    #                 break
    #         if i + length +1 >= len(text_id):
    #             break
    
    # # count for if pred_T in the original text
    # for pred_t_id in pred_T_ids:
    #     length = len(pred_t_id)
    #     for i in range(len(text_id)):
    #         for j in range(length):
    #             if text_id[i+j+1] == pred_t_id[:j+1]:
    #                 if j+1 == length:
    #                     num_predT_in_original += 1
    #             else:
    #                 if j+1 > length/2:
    #                     print(tokenizer.decode(pred_t_id[:j+1]))
    #                     num_predT_over50_in_original += 1
    #                 break
    #         if i + length +1 >= len(text_id):
    #             break
    
    # # count for if gold_T in the original text
    # for gold_t_id in gold_T_ids:
    #     length = len(gold_t_id)
    #     for i in range(len(text_id)):
    #         for j in range(length):
    #             if text_id[i+j+1] == gold_t_id[:j+1]:
    #                 if j+1 == length:
    #                     num_predT_in_golden += 1
    #             else:
    #                 break
    #         if i + length +1 >= len(text_id):
    #             break
    
    # # count for if gold_D in the original text
    # for gold_d_id in gold_D_ids:
    #     length = len(gold_d_id)
    #     for i in range(len(text_id)):
    #         for j in range(length):
    #             if text_id[i+j+1] == gold_d_id[:j+1]:
    #                 if j+1 == length:
    #                     num_predD_in_golden += 1
    #             else:
    #                 break
    #         if i + length +1 >= len(text_id):
    #             break

train_dataset

In [12]:
len(golden) == len(pmids)

True

In [15]:
num_gold_D = 0
num_gold_T = 0


num_predD_in_original = 0
num_predT_in_original = 0
# # if there are more than 50% prefix tokens of a span is in the original text, count it
# num_predD_over50_in_original = 0
# num_predT_over50_in_original = 0
# partial in the golden means the model didn't generate the whole span.
num_goldD_in_original = 0
num_goldT_in_original = 0

for id in pmids:
    # only use lower() to nomalize the text
    gold_Ds = list(set([triple['drug'].lower() for triple in golden[id]['triples']]))
    gold_Ts = list(set([triple['target'].lower() for triple in golden[id]['triples']]))
    text = (golden[id]['title'] + " " + golden[id]['abstract']).lower()
    
    num_gold_D += len(gold_Ds)
    num_gold_T += len(gold_Ts)

    predT_not_in_original = []

    # count for if god_D in the original text
    for gold_D in gold_Ds:
        if gold_D in text:
            num_goldD_in_original += 1

    # count for if god_T in the original text
    for gold_T in gold_Ts:
        if gold_T in text:
            num_goldT_in_original += 1

In [16]:
# print num_predD_in_original, num_predT_in_original, num_predD_over50_in_original, num_predT_over50_in_original, num_predD_in_golden = 0, num_predT_in_golden with their lables
# print("num_predD_in_original: ", num_predD_in_original)
# print("num_predT_in_original: ", num_predT_in_original)
print("num_goldD_in_original: ", num_goldD_in_original)
print("num_goldT_in_original: ", num_goldT_in_original)
# print("num__pred_D: ", num_pred_D)
# print("num_pred_T: ", num_pred_T)
print("num_gold_D: ", num_gold_D)
print("num_gold_T: ", num_gold_T)

num_goldD_in_original:  8369
num_goldT_in_original:  1535
num_gold_D:  19426
num_gold_T:  17179


In [17]:
# print(f"For pred_D:\n{num_predD_in_original} / {num_pred_D} : {round(num_predD_in_original/num_pred_D, 4)}")
# print(f"For pred_T:\n{num_predT_in_original} / {num_pred_T} : {round(num_predT_in_original/num_pred_T, 4)}")
print(f"For gold_D:\n{num_goldD_in_original} / {num_gold_D} : {round(num_goldD_in_original/num_gold_D, 4)}")
print(f"For gold_T:\n{num_goldT_in_original} / {num_gold_T} : {round(num_goldT_in_original/num_gold_T, 4)}")

For gold_D:
8369 / 19426 : 0.4308
For gold_T:
1535 / 17179 : 0.0894


In [101]:
with open('analysis/predT_not_in_original_pmid_predTs.json', 'w') as writer:
    json.dump(predT_not_in_original_pmid_predTs, writer, indent=2)